In [1]:
import pandas as pd
import numpy as np
import xgboost
import gc
import Evrecsys

In [2]:
#Import data
order_products_prior = pd.read_csv("order_products__prior.csv", dtype={
            'order_id': np.int32,
            'product_id': np.uint16,
            'add_to_cart_order': np.int16,
            'reordered': np.int8})
orders = pd.read_csv("orders.csv", dtype={
        'order_id': np.int32,
        'user_id': np.int32,
        'eval_set': 'category',
        'order_number': np.int16,
        'order_dow': np.int8,
        'order_hour_of_day': np.int8,
        'days_since_prior_order': np.float32})

products = pd.read_csv("products.csv", dtype={
        'product_id': np.uint16,
        'order_id': np.int32,
        'aisle_id': np.uint8,
        'department_id': np.uint8},
        usecols=['product_id', 'aisle_id', 'department_id'])

orders=orders.loc[orders['eval_set']=='prior']

#We will work with 5000 users, last order will be in test set
number_users=5000
users=range(1,number_users+1)
orders_set=orders[orders["user_id"].isin(users)]
idx_test = orders_set.groupby(['user_id'])['order_number'].transform(max) == orders_set['order_number']
orders_set_test=orders_set[idx_test]

orders_set_testlist=np.unique(orders_set_test.order_id)
orders_set_train = orders_set[-orders_set["order_id"].isin(orders_set_testlist)]
orders_set_trainlist=np.unique(orders_set_train.order_id)
train= order_products_prior[order_products_prior["order_id"].isin(orders_set_trainlist)]
test=order_products_prior[order_products_prior["order_id"].isin(orders_set_testlist)]
train = pd.merge(train, orders_set_train, on='order_id', how='left')
test=pd.merge(test, orders_set_test, on='order_id', how='left')

print('Train set has %f orders',len(np.unique(train.order_id)))
print('Test set has %f orders',len(np.unique(test.order_id)))
print('Train set has %f users',len(np.unique(train.user_id)))
print('Test set has %f users',len(np.unique(test.user_id)))

Train set has %f orders 71832
Test set has %f orders 5000
Train set has %f users 5000
Test set has %f users 5000


In [3]:
orders_set_train.head()

order_id  user_id eval_set  order_number  order_dow  order_hour_of_day  \
0   2539329        1    prior             1          2                  8   
1   2398795        1    prior             2          3                  7   
2    473747        1    prior             3          3                 12   
3   2254736        1    prior             4          4                  7   
4    431534        1    prior             5          4                 15   

   days_since_prior_order  
0                     NaN  
1                    15.0  
2                    21.0  
3                    29.0  
4                    28.0

In [4]:
train.head()

order_id  product_id  add_to_cart_order  reordered  user_id eval_set  \
0         8       23423                  1          1     3107    prior   
1        74       46667                  1          1     3321    prior   
2        74       14129                  2          1     3321    prior   
3        74       11136                  3          1     3321    prior   
4        74       27247                  4          1     3321    prior   

   order_number  order_dow  order_hour_of_day  days_since_prior_order  
0             5          4                  6                    17.0  
1            31          5                 21                    14.0  
2            31          5                 21                    14.0  
3            31          5                 21                    14.0  
4            31          5                 21                    14.0

In [5]:
test.head()

order_id  product_id  add_to_cart_order  reordered  user_id eval_set  \
0        40       10070                  1          1      382    prior   
1        40       42450                  2          1      382    prior   
2        40       33198                  3          1      382    prior   
3        40       34866                  4          1      382    prior   
4       504       19894                  1          0     2201    prior   

   order_number  order_dow  order_hour_of_day  days_since_prior_order  
0            29          1                 15                    23.0  
1            29          1                 15                    23.0  
2            29          1                 15                    23.0  
3            29          1                 15                    23.0  
4            10          3                 17                    22.0

In [6]:
user_product = train.groupby(['user_id', 'product_id']).size().reset_index()

In [38]:
for i in np.unique(test.user_id):
    print(i)
    user_product_i=user_product[user_product['user_id']==i]
    test_i=test[test['user_id']==i]
    set1 = set(np.unique(user_product_i.product_id))
    set2 = set(np.unique(test_i.product_id))
    missing =  pd.DataFrame.from_dict(list(sorted(set1 - set2)))
    print(missing)
    for j in range(len(missing)): 
        a=missing[0][j]
        print(a)
        test=test.append({'order_id':test_i.order_id[test_i.index[0]], 'product_id':a, 'add_to_cart_order':0, 'reordered':0, 'user_id':i,
       'eval_set':0, 'order_number':test_i.order_number[test_i.index[0]], 'order_dow':test_i.order_dow[test_i.index[0]], 'order_hour_of_day':test_i.order_hour_of_day[test_i.index[0]],
       'days_since_prior_order':test_i.days_since_prior_order[test_i.index[0]]},ignore_index=True)
        
    
test=test.fillna(0)

1
       0
0  10326
1  13176
2  14084
3  17122
4  26088
5  26405
6  30450
7  41787
8  49235
10326
13176
14084
17122
26088
26405
30450
41787
49235
2
        0
0      23
1      79
2    2002
3    3151
4    4071
5    4957
6    5212
7    5322
8    5450
9    5869
10   5907
11   8138
12   8296
13   8479
14   9124
15   9681
16  10305
17  12000
18  12258
19  13176
20  13351
21  13742
22  14306
23  14553
24  15841
25  16521
26  16797
27  17224
28  17758
29  17872
..    ...
56  33276
57  33957
58  34688
59  35917
60  36287
61  36735
62  37646
63  38656
64  39877
65  40198
66  40571
67  41787
68  42342
69  42356
70  44303
71  45066
72  45613
73  45948
74  46676
75  46886
76  47144
77  47526
78  47553
79  47766
80  47792
81  48099
82  48110
83  48210
84  49273
85  49451

[86 rows x 1 columns]
23
79
2002
3151
4071
4957
5212
5322
5450
5869
5907
8138
8296
8479
9124
9681
10305
12000
12258
13176
13351
13742
14306
14553
15841
16521
16797
17224
17758
17872
18961
19051
19057
19240
20084
20574
21150
21227
2

10017
12069
13780
17794
21903
22247
27104
27336
28199
28985
30391
30406
31772
33346
35140
36198
36772
37107
37687
40706
41950
43014
43858
44359
45073
45229
46667
46709
48171
48745
49478
17
        0
0     812
1    1073
2    1774
3    2927
4    4591
5    5077
6    5128
7    5748
8    6212
9    6334
10   7026
11   7992
12   8730
13   9176
14   9387
15   9634
16   9641
17  10300
18  10921
19  11919
20  12513
21  12720
22  12855
23  15125
24  15820
25  15844
26  15925
27  16188
28  16486
29  17040
..    ...
45  29791
46  30992
47  31268
48  32498
49  33560
50  35419
51  36130
52  36463
53  36552
54  36736
55  38444
56  38618
57  38760
58  40203
59  40592
60  40844
61  42356
62  43986
63  44234
64  44265
65  44492
66  45190
67  46844
68  47031
69  47141
70  47577
71  47940
72  48544
73  48682
74  49131

[75 rows x 1 columns]
812
1073
1774
2927
4591
5077
5128
5748
6212
6334
7026
7992
8730
9176
9387
9634
9641
10300
10921
11919
12513
12720
12855
15125
15820
15844
15925
16188
16486
17040
17762


7021
8025
8076
8503
8529
8615
8670
8697
10383
10644
11576
13380
14950
14992
16137
17794
19395
20114
20588
20697
21137
21174
21513
21903
22451
22935
23032
23044
23338
23400
23644
24382
24622
24759
24952
24964
25588
25659
25949
26128
26209
26604
27086
27156
27323
28204
28745
31215
31343
31717
32049
32689
32734
32828
33731
34551
34969
36135
37192
37220
38689
39076
39831
40706
41338
41483
42265
42557
42768
42828
44142
44761
44910
46667
47144
47209
47766
48105
49175
49236
29
        0
0     169
1    1261
2    1330
3    2839
4    3128
5    3696
6    5210
7    7930
8    8523
9    8806
10   9875
11  10500
12  11586
13  12720
14  12879
15  13129
16  15293
17  17817
18  19541
19  20874
20  21410
21  21496
22  21645
23  22259
24  26360
25  27612
26  28862
27  28993
28  29267
29  29628
30  30389
31  30695
32  31608
33  32987
34  33027
35  33161
36  33973
37  34749
38  35507
39  36543
40  37645
41  38053
42  38233
43  39185
44  40214
45  40592
46  41210
47  41298
48  41653
49  42258
50  42551
51  4

18594
18840
18849
18908
19019
19816
21376
21709
21846
21938
22922
22935
23233
23734
23909
24499
26133
26209
26369
26620
26738
27086
27344
27509
28123
29311
31343
31506
32433
32655
32691
32839
34635
35383
37119
38012
40203
42342
43304
44769
45437
47209
47672
39
        0
0    1870
1    5373
2    5450
3    6567
4    8174
5    8203
6    9076
7   12857
8   17794
9   18479
10  19019
11  19478
12  21019
13  21295
14  21903
15  23291
16  24852
17  26683
18  27012
19  27735
20  28204
21  28553
22  28849
23  30450
24  30489
25  30962
26  32653
27  33731
28  34584
29  37642
30  39928
31  40002
32  43647
33  43768
34  44359
35  44910
36  46906
37  47734
38  49191
1870
5373
5450
6567
8174
8203
9076
12857
17794
18479
19019
19478
21019
21295
21903
23291
24852
26683
27012
27735
28204
28553
28849
30450
30489
30962
32653
33731
34584
37642
39928
40002
43647
43768
44359
44910
46906
47734
49191
40
        0
0    2238
1    4193
2    5322
3    5450
4    5699
5    9290
6   11777
7   13740
8   13870
9   13877

40063
40422
41400
41787
42489
45920
46061
46149
46516
49083
49235
49243
53
        0
0     377
1    8615
2   11210
3   13245
4   14168
5   15804
6   16797
7   24339
8   25544
9   27796
10  31506
11  35053
12  35412
13  36180
14  36780
15  37609
16  43086
17  44142
18  45541
19  48364
377
8615
11210
13245
14168
15804
16797
24339
25544
27796
31506
35053
35412
36180
36780
37609
43086
44142
45541
48364
54
         0
0      890
1      952
2     1025
3     1063
4     1158
5     1359
6     1511
7     1529
8     1999
9     2314
10    2447
11    2450
12    3464
13    3494
14    3793
15    3989
16    4392
17    4562
18    4679
19    4796
20    4799
21    5024
22    5025
23    5337
24    5746
25    5769
26    6129
27    6141
28    6638
29    6873
..     ...
216  44142
217  44422
218  44449
219  44514
220  44626
221  44706
222  44912
223  45007
224  45066
225  45535
226  45582
227  45771
228  45801
229  45918
230  46045
231  46667
232  46802
233  46906
234  46979
235  47325
236  47626
237  47752
2

...

42443
43086
43122
43165
43234
43424
43726
44359
44636
44683
44910
45007
45066
45264
45464
45650
46107
46206
46665
46676
46979
47042
47418
47734
47788
47866
48086
48357
48364
48775
49075
49111
49235
49236
49383
4950
        0
0    1833
1    2581
2    3761
3    4781
4    4870
5    5250
6    5337
7    5450
8    6348
9    6599
10   6871
11   6987
12   7662
13  10599
14  12576
15  13774
16  13870
17  13996
18  16185
19  16262
20  16406
21  17284
22  19006
23  19907
24  21006
25  21062
26  21653
27  21847
28  22290
29  22379
..    ...
37  28620
38  29045
39  29801
40  30117
41  30908
42  31506
43  31801
44  31974
45  32052
46  33729
47  35121
48  35958
49  36608
50  36724
51  38164
52  38809
53  39877
54  39989
55  40411
56  40541
57  41080
58  41621
59  42828
60  44292
61  44477
62  46828
63  47873
64  48642
65  48988
66  49235

[67 rows x 1 columns]
1833
2581
3761
4781
4870
5250
5337
5450
6348
6599
6871
6987
7662
10599
12576
13774
13870
13996
16185
16262
16406
17284
19006
19907
21006
21062

4605
5450
5857
6139
7831
8707
8955
10673
11461
12323
12697
13212
17794
18412
18439
22183
22296
22524
22823
23032
23360
23888
25124
25760
27662
27796
28407
28480
29646
30500
30645
31506
32433
34092
34103
34878
35181
35970
36099
38154
39139
41352
41372
43262
44085
44566
45566
46434
46749
47626
48093
4964
        0
0    1468
1    5597
2    5707
3    7018
4    8518
5   12890
6   15649
7   16083
8   20431
9   20655
10  21511
11  21903
12  26128
13  26475
14  27122
15  28918
16  28985
17  30169
18  31805
19  33401
20  35270
21  35547
22  38028
23  38256
24  38400
25  39024
26  41774
27  46047
28  46331
29  47766
1468
5597
5707
7018
8518
12890
15649
16083
20431
20655
21511
21903
26128
26475
27122
28918
28985
30169
31805
33401
35270
35547
38028
38256
38400
39024
41774
46047
46331
47766
4965
        0
0     424
1     432
2    2966
3    5876
4    6740
5    7175
6    9839
7   15700
8   17355
9   19660
10  21903
11  24852
12  24964
13  28204
14  31343
15  33041
16  33929
17  34824
18  42736
424
43

881
1187
1390
1599
2475
2658
2923
4138
4865
4920
5550
5782
5818
5897
6991
7667
7682
8230
10054
11819
13540
13954
14183
14197
14252
14381
14897
15290
17615
18301
19145
19488
21417
21737
21938
22025
22658
23165
23740
24135
25963
26124
26882
27933
28871
31960
32104
32762
33178
33704
33771
33950
34064
34287
34358
34582
34678
35108
36545
37065
37113
37710
37722
38318
38365
38483
38593
39315
40348
41950
42114
43744
43772
44142
44359
44375
44538
44744
44765
45149
45705
46069
46129
46421
46979
48131
49269
49683
4973
        0
0     890
1    1468
2    1529
3    2579
4    2846
5    4302
6    4605
7    5025
8    5621
9    5876
10   7500
11   8193
12   9387
13   9472
14   9808
15   9839
16  10385
17  11390
18  11755
19  12341
20  12614
21  13198
22  13212
23  13249
24  14159
25  15143
26  16325
27  17468
28  17794
29  17872
..    ...
44  30489
45  30720
46  30953
47  31506
48  33401
49  33884
50  34126
51  34358
52  34530
53  34969
54  35973
55  36695
56  37107
57  37766
58  38777
59  39054
60  39

18531
18609
18963
19057
19065
21019
22198
22234
22950
22971
24838
27086
27521
27966
28156
28204
29487
30391
31328
31338
31562
32689
32864
33554
33731
34526
35168
36090
36389
36870
37454
37642
39275
40709
40992
41220
43295
43803
43830
44359
44953
45123
45694
46667
46802
46979
47008
47766
47866
48775
4981
        0
0    1640
1    2966
2    2979
3    5435
4   10060
5   11782
6   13424
7   17429
8   18234
9   18829
10  21137
11  22008
12  23898
13  24818
14  29199
15  32597
16  35168
17  36149
18  38226
19  38273
20  38837
21  39275
22  43621
23  43789
24  47766
1640
2966
2979
5435
10060
11782
13424
17429
18234
18829
21137
22008
23898
24818
29199
32597
35168
36149
38226
38273
38837
39275
43621
43789
47766
4982
        0
0    2449
1    9007
2   11759
3   13176
4   13948
5   16139
6   21137
7   21288
8   21903
9   25588
10  30450
11  33198
12  34208
13  36534
14  43352
2449
9007
11759
13176
13948
16139
21137
21288
21903
25588
30450
33198
34208
36534
43352
4983
        0
0    2664
1    3962
2

5794
7139
8277
9387
10251
12362
13176
13740
14127
15604
16768
16936
19057
19660
20169
20555
21846
22365
23405
24852
25340
25522
26209
26604
27086
27117
27464
27730
27845
28199
28204
31205
36418
37067
37208
37646
38557
39101
39475
40411
41387
41774
42944
44632
46676
46906
48722
49235
4994
         0
0      683
1      766
2     1086
3     1511
4     1712
5     2519
6     2906
7     2974
8     4367
9     4962
10    4966
11    5189
12    5257
13    5275
14    5787
15    5876
16    6036
17    7158
18    7751
19    7861
20    7925
21    7963
22    8277
23    8518
24    8536
25    9018
26    9252
27   10241
28   10895
29   10957
..     ...
140  39604
141  39832
142  40002
143  40174
144  40706
145  40931
146  41057
147  41709
148  41966
149  42460
150  43129
151  43565
152  43685
153  43772
154  43902
155  44548
156  44954
157  45840
158  46260
159  46347
160  46584
161  46820
162  46907
163  47772
164  48524
165  48659
166  49185
167  49222
168  49235
169  49544

[170 rows x 1 columns]
683
7

In [52]:
#test.to_csv('test_5000_complete')

In [6]:
test=pd.read_csv("test_5000_complete.csv")

/home/grecia/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (6) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [8]:
test=test.drop(test.columns[0], axis=1)
test.head()

order_id  product_id  add_to_cart_order  reordered  user_id eval_set  \
0      40.0     10070.0                1.0        1.0    382.0    prior   
1      40.0     42450.0                2.0        1.0    382.0    prior   
2      40.0     33198.0                3.0        1.0    382.0    prior   
3      40.0     34866.0                4.0        1.0    382.0    prior   
4     504.0     19894.0                1.0        0.0   2201.0    prior   

   order_number  order_dow  order_hour_of_day  days_since_prior_order  pred  
0          29.0        1.0               15.0                    23.0     1  
1          29.0        1.0               15.0                    23.0     1  
2          29.0        1.0               15.0                    23.0     1  
3          29.0        1.0               15.0                    23.0     1  
4          10.0        3.0               17.0                    22.0     1

In [9]:
param = {'max_depth':10, 
         'eta':0.02,
         'colsample_bytree':0.4,
         'subsample':0.75,
         'silent':1,
         'nthread':27,
         'eval_metric':'logloss',
         'objective':'binary:logistic',
         'tree_method':'hist'
         }

y_train = train['reordered']
X_train = train.drop(['reordered','eval_set', 'add_to_cart_order'], axis=1)

y_test = test['reordered']
X_test = test.drop(['reordered','pred','eval_set','add_to_cart_order'], axis=1)

In [10]:
dtrain = xgboost.DMatrix(X_train, label=y_train)
dtest = xgboost.DMatrix(X_test)

In [11]:
model = xgboost.train(param, dtrain)

[11:01:38] Tree method is selected to be 'hist', which uses a single updater grow_fast_histmaker.


In [12]:
predict_labels = model.predict(dtest)

In [13]:
predict_labels=(predict_labels>0.50)*1

In [14]:
test['pred']=predict_labels

In [15]:
true = test[test['reordered']==1].groupby('order_id').aggregate({'product_id':lambda x: list(x)})
pred= test[test['pred']==1].groupby('order_id').aggregate({'product_id':lambda x: list(x)})

In [19]:
import Evrecsys
results=[]
#Xgboost
sum_recall=0
sum_precision=0
sum_fscore=0
n=len(true)
for i in orders_set_test.order_id:
    print(i)
    if i in true.index:
        y=true['product_id'][i]
    else:
        y='nan'
    if i in pred.index:
        y_hat=pred['product_id'][i][:10]
    else:
        y_hat='nan'
        
    p,r,f1=Evrecsys.calculate_prf(y,y_hat)
    sum_precision=sum_precision+p
    sum_recall=sum_recall+r
    sum_fscore=sum_fscore+f1

results.append(['xgboost',sum_recall/n,sum_precision/n ,sum_fscore/n])


2550362
839880
1402502
2557754
157374
998866
2452257
2570360
1830137
1353310
1468214
221248
1789302
3394109
487368
2000615
3350883
441977
86918
2741696
3341737
2647850
1072926
173172
258751
232721
1573122
1978052
1647841
3333738
1765409
1210985
1537903
2344038
2903057
2710884
1727614
2479273
2754717
1145465
3083886
3034563
2770903
2699868
1902833
2009771
1899315
555834
1250641
103726
2151817
1588305
227361
596690
2206148
1836190
2676852
1976929
1625716
1597833
1713067
479208
443742
3129760
864720
932035
1931044
3117228
2550244
29902
1551092
2520276
2499247
3391303
1657089
380972
737247
1009350
1882917
2001654
1928924
3144004
1342998
2128144
2430990
2549405
1962113
2062476
3025545
440272
2317062
840547
2926108
259674
2855192
784032
2921005
1993729
2326743
2875733
1285684
2531610
221085
1645432
3204356
355095
2091156
505076
1382150
2781137
2552531
3378311
1197224
1798152
2617020
2224236
2116043
753212
1776217
3273029
2929824
3024894
1906256
2776620
3060658
32138
1964699
2790818
1019891
2

245369
2861873
2620779
1086086
3273437
2484915
532733
2594019
1932862
2723974
793145
2019919
1441982
3146204
2525124
2905156
436582
1841255
173222
2718802
1329118
374097
2459545
1047860
71989
897790
1286799
448934
70418
3334297
2212108
689580
2721182
842749
753127
318967
1227787
123081
1135897
1254296
155145
2399832
1093644
3158146
1732288
2260569
309396
1395018
1302368
1251412
2649936
688067
942255
1676425
894121
2650278
455955
1785861
1132903
970029
3255314
3058565
793704
1645097
1272996
2285225
776735
1031745
745340
997090
596622
170877
511691
674018
655058
2642792
1359237
588352
3420215
3378856
1327470
1455189
2154097
397368
1337236
2457776
782537
677213
1123735
1988017
643453
1659440
2267702
636825
2633386
1797072
1287375
247400
1525211
1472514
2443753
369341
454536
2820228
625605
495127
1203420
1617061
124056
90999
1476406
2451386
1833467
1085107
55597
3379854
967948
138070
2624549
1354687
796349
570765
2442148
1264995
1040447
1780152
2657447
1452302
913838
2499080
1268968
333874

1713430
3384353
3387239
2047762
3008223
640965
1886727
1367106
2004965
3368461
763545
1957085
1859921
2574322
385424
2237549
1665584
2399196
2126176
1941075
1954774
3235644
2372356
3179211
3305059
2367239
1473338
1919811
2896551
1622434
217249
2729392
3233340
2872207
1818227
2773724
3096255
119378
2573588
2402223
2016977
1610099
1935729
1423938
832
1700478
2464104
2475685
2019243
2158220
2449046
771677
2753536
1191920
2136898
1054131
3165463
1570252
2067753
1995436
1834922
2326570
1740752
1307694
2964747
1202145
3004336
1871886
1368380
183598
3176216
852045
2859868
2702002
2347513
560955
1469317
3388024
2885877
361144
1345891
2912984
1251117
3127556
732164
170054
3008416
207144
489941
813756
2374551
42445
2255854
2617025
1878819
3078347
815640
1166764
842322
1638059
1133075
2479867
1223221
961510
1451662
2133545
305110
2687224
2743525
1392001
1197680
1869949
2011429
683491
2441036
819312
3373451
2401079
2243362
1469250
518018
3318893
3224435
369511
1678207
1741194
1140083
663210
174376

NameError: name 'sum_auc' is not defined

In [24]:
sum_fscore/n

0.5422445794740783